In [140]:
!git clone https://gitlab.com/1byxero/deep_learning_systems.git
!pip install librosa
from IPython import display


from os.path import join

import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torch import optim

import librosa

common_path = join('deep_learning_systems','Assignment 1', 'data')
train_clean_path = join(common_path,'train_clean_male.wav')
train_dirty_path = join(common_path,'train_dirty_male.wav')
test_x_01_path = join(common_path,'test_x_01.wav')
test_x_02_path = join(common_path,'test_x_02.wav')

s, sr=librosa.load(train_clean_path, sr=None)
S=librosa.stft(s, n_fft=1024, hop_length=512)
sn, sr=librosa.load(train_dirty_path, sr=None)
X=librosa.stft(sn, n_fft=1024, hop_length=512)

S_abs = torch.tensor(np.abs(S)).float().T
X_abs = torch.tensor(np.abs(X)).float().T

fatal: destination path 'deep_learning_systems' already exists and is not an empty directory.


In [269]:
class AudioDataset(Dataset):
    def __init__(self, data, label):
        self.sample = data.view(data.shape[0],1,19,513)
        self.label = label
        
    
    def __len__(self):
        if len(self.sample) == len(self.label):
            return len(self.sample)
    
    def __getitem__(self, idx):
        return self.sample[idx], self.label[idx]

ns = torch.distributions.Normal(0, 0.00005)

noise = ns.sample((19,513))
noised_input = torch.cat((noise, X_abs))
image_arr = []

for i in range(19, noised_input.shape[0]):
    image_arr.append(noised_input[i-19:i,:].view(1,19,513))
    
image_of_audio = torch.cat(image_arr)
print(image_of_audio.shape)

ds = AudioDataset(image_of_audio, S_abs)
train_loader = DataLoader(ds, batch_size=512, shuffle=False, num_workers=2)



class Net(nn.Module):

    def __init__(self):
        super(Net, self).__init__()
        self.c1d1 = nn.Conv2d(1, 2, 9, 2)
        self.c1d2 = nn.Conv2d(2, 6, 6, 2)
        self.ff1 = nn.Linear(744, 600)
        self.out = nn.Linear(600, 513)

    def forward(self, x):
        x = F.relu(self.c1d1(x))
        x = F.relu(self.c1d2(x))
        x = F.relu(self.ff1(x.view(-1, 744)))
        x = F.relu(self.out(x))
        return x
  
def init_weights(layer):
    if isinstance(layer, nn.Linear):
        nn.init.xavier_normal_(layer.weight.data)
        nn.init.zeros_(layer.bias.data)

net = Net()
net.apply(init_weights)
print(net)

learning_rate = 1e-3
criterion = nn.MSELoss()
optimizer = optim.Adam(net.parameters(), lr=learning_rate)

torch.Size([2459, 19, 513])
Net(
  (c1d1): Conv2d(1, 2, kernel_size=(9, 9), stride=(2, 2))
  (c1d2): Conv2d(2, 6, kernel_size=(6, 6), stride=(2, 2))
  (ff1): Linear(in_features=744, out_features=600, bias=True)
  (out): Linear(in_features=600, out_features=513, bias=True)
)


In [270]:
epoch_count = 150
for epoch in range(epoch_count):
    running_loss = 0.0
    
    for index, data in enumerate(train_loader):
        inputs, labels = data
        optimizer.zero_grad() #understand why is this required

        outputs = net(inputs)
        
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        
        running_loss += loss.item()
        if index % 5 == 4:    # print every 5 mini-batches
            print('[%d, %5d] loss: %.6f' %
                  (epoch + 1, index + 1, running_loss / 5))
            running_loss = 0.0

print("Done training")

[1,     5] loss: 0.090910
[2,     5] loss: 0.085202
[3,     5] loss: 0.084310
[4,     5] loss: 0.083410
[5,     5] loss: 0.082682
[6,     5] loss: 0.081726
[7,     5] loss: 0.080566
[8,     5] loss: 0.078985
[9,     5] loss: 0.076841
[10,     5] loss: 0.074258
[11,     5] loss: 0.071603
[12,     5] loss: 0.069150
[13,     5] loss: 0.067201
[14,     5] loss: 0.065480
[15,     5] loss: 0.063777
[16,     5] loss: 0.062148
[17,     5] loss: 0.060640
[18,     5] loss: 0.059221
[19,     5] loss: 0.057873
[20,     5] loss: 0.056550
[21,     5] loss: 0.055257
[22,     5] loss: 0.053936
[23,     5] loss: 0.052605
[24,     5] loss: 0.051242
[25,     5] loss: 0.049896
[26,     5] loss: 0.048571
[27,     5] loss: 0.047293
[28,     5] loss: 0.046053
[29,     5] loss: 0.044872
[30,     5] loss: 0.043766
[31,     5] loss: 0.042808
[32,     5] loss: 0.042074
[33,     5] loss: 0.042409
[34,     5] loss: 0.041170
[35,     5] loss: 0.041123
[36,     5] loss: 0.038918
[37,     5] loss: 0.038065
[38,     5

Another network with following configuration gave 5 snr on train audio.

1. Conv layer with 2 output channels and 7x7 kernel size with stride 2
2. Conv layer with 4 output channels and 5x kernel size with stride 2
3. followed by 2 Fully connected layers

Both networks saturated after 150ish epochs however. Current Network performed better when sound perception was considered

In [271]:
t, tr=librosa.load(train_dirty_path , sr=None)
T_one=librosa.stft(t, n_fft=1024, hop_length=512)
T_one_mod = torch.tensor(np.abs(T_one)).float().T

def get_cleaned_signal(signal, output):
    op = signal/np.abs(signal)
    op = np.multiply(op,output.numpy())
    return op
    
output_list_one = []

with torch.no_grad():
    for batch in train_loader:
        data, label = batch        
        op_one = net(data)
        output_list_one.append(op_one)    
ops = torch.cat(output_list_one)

clean_one = get_cleaned_signal(T_one, ops.t())
op_istft = librosa.core.istft(clean_one, hop_length=512)

print("SNR is {}".format(
        np.dot(t,t.T)/np.dot(
        (t[:len(op_istft)]-op_istft),
        (t[:len(op_istft)]-op_istft).T
    )
))

display.display(display.Audio(train_dirty_path,rate=tr))
#this is the input file
display.display(display.Audio(data=op_istft,rate=tr))
# librosa.output.write_wav('test_s_01_recons.wav', op_istft, sr)

SNR is 4.176331043243408


In [0]:
t, tr=librosa.load(test_x_01_path , sr=None)
T_one=librosa.stft(t, n_fft=1024, hop_length=512)
T_one_mod = torch.tensor(np.abs(T_one)).float().T

t2, tr2=librosa.load(test_x_02_path , sr=None)
T_two=librosa.stft(t2, n_fft=1024, hop_length=512)
T_two_mod = torch.tensor(np.abs(T_two)).float().T


noise = ns.sample((19,513))
noised_input = torch.cat((noise, T_one_mod))
noised_input2 = torch.cat((noise, T_two_mod))
image_arr = []
image_arr2 = []


for i in range(19, noised_input.shape[0]):
    image_arr.append(noised_input[i-19:i,:].view(1,19,513))

for i in range(19, noised_input2.shape[0]):
    image_arr2.append(noised_input2[i-19:i,:].view(1,19,513))
    
image_of_audio = torch.cat(image_arr)
image_of_audio2 = torch.cat(image_arr2)


testset_one = AudioDataset(image_of_audio, image_of_audio)
testset_two = AudioDataset(image_of_audio2, image_of_audio2)


test_loader = DataLoader(testset_one, batch_size=50, shuffle=False, num_workers=2)
output_list_one = []

with torch.no_grad():
    for batch in test_loader:
        data, label = batch        
        op_one = net(data)
        output_list_one.append(op_one)    
ops = torch.cat(output_list_one)

clean_one = get_cleaned_signal(T_one, ops.t())
op_istft = librosa.core.istft(clean_one, hop_length=512)


test_loader2 = DataLoader(testset_two, batch_size=50, shuffle=False, num_workers=2)
output_list_two = []

with torch.no_grad():
    for batch in test_loader2:
        data, label = batch        
        op_one = net(data)
        output_list_two.append(op_one)    
ops2 = torch.cat(output_list_two)

clean_one2 = get_cleaned_signal(T_two, ops2.t())
op_istft2 = librosa.core.istft(clean_one2, hop_length=512)


In [276]:
#this is the input file
display.display(display.Audio(test_x_01_path,rate=tr))
#this is the input file
display.display(display.Audio(data=op_istft,rate=tr))
librosa.output.write_wav('test_s_01_recons.wav', op_istft, sr)

In [277]:
#this is the input file
display.display(display.Audio(data=test_x_02_path,rate=tr2))
#this is the synthesized file
display.display(display.Audio(data=op_istft2,rate=tr2))
librosa.output.write_wav('test_s_02_recons.wav', op_istft2, tr)

In [0]:
from google.colab import files
files.download('test_s_01_recons.wav') 

In [0]:
files.download('test_s_02_recons.wav') 